In [1]:
import pandas as pd

data = pd.read_csv('IMDB-Dataset.csv', error_bad_lines=False);

# split positive and negative sentiment reviews
pos_reviews = data[data.sentiment == "positive"]
neg_reviews = data[data.sentiment == "negative"]

pos_data = pos_reviews[['review']]
pos_data['index'] = pos_data.index
pos_documents = pos_data

neg_data = neg_reviews[['review']]
neg_data['index'] = neg_data.index
neg_documents = neg_data

# showing that the reviews were correctly split by sentiment
print(len(pos_documents))
print(pos_documents[:5])
print(len(neg_documents))
print(neg_documents[:5])

25000
                                              review  index
0  One of the other reviewers has mentioned that ...      0
1  A wonderful little production. <br /><br />The...      1
2  I thought this was a wonderful way to spend ti...      2
4  Petter Mattei's "Love in the Time of Money" is...      4
5  Probably my all-time favorite movie, a story o...      5
25000
                                               review  index
3   Basically there's a family where a little boy ...      3
7   This show was an amazing, fresh & innovative i...      7
8   Encouraged by the positive comments about this...      8
10  Phil the Alien is one of those quirky films wh...     10
11  I saw this movie when I was about 12 when it c...     11


In [2]:
from nltk.corpus import stopwords
import re

stop_words = list(set(stopwords.words('english')))

'''Positive Data'''
# Remove punctuation using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: x.lower())
'''Negative Data'''
# Remove punctuation using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: x.lower())

In [3]:
from wordcloud import WordCloud

print("Word Cloud generated from positive reviews with minimal preprocessing:")
long_string = " ".join(pos_documents.review_processed)

wordcloud = WordCloud().generate(long_string)
image = wordcloud.to_image()
image.show()

print("Word Cloud generated from negative reviews with minimal preprocessing:")
long_string = " ".join(neg_documents.review_processed)
wordcloud = WordCloud().generate(long_string)
image = wordcloud.to_image()
image.show()

Word Cloud generated from positive reviews with minimal preprocessing:
Word Cloud generated from negative reviews with minimal preprocessing:


In [4]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(2018)
import nltk

stemmer = SnowballStemmer("english")
def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))


def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

In [5]:
pos_processed_documents = pos_documents['review_processed'].map(preprocess)
print("Positive reviews after lemmatizing and stemming:")
print(len(pos_processed_documents))
print(pos_processed_documents[:10])

neg_processed_documents = neg_documents['review_processed'].map(preprocess)
print("\nNegative reviews after lemmatizing and stemming:")
print(len(neg_processed_documents))
print(neg_processed_documents[:10])

Positive reviews after lemmatizing and stemming:
25000
0     [review, mention, watch, episod, hook, right, ...
1     [wonder, littl, product, film, techniqu, unass...
2     [think, wonder, spend, time, summer, weekend, ...
4     [petter, mattei, love, time, money, visual, st...
5     [probabl, time, favorit, movi, stori, selfless...
6     [sure, like, resurrect, date, seahunt, seri, t...
9     [like, origin, wrench, laughter, like, movi, y...
14    [fantast, movi, prison, famous, actor, georg, ...
16    [film, simpli, remak, film, fail, captur, flav...
18    [rememb, film, film, watch, cinema, pictur, da...
Name: review_processed, dtype: object

Negative reviews after lemmatizing and stemming:
25000
3     [basic, famili, littl, jake, think, zombi, clo...
7     [amaz, fresh, innov, idea, air, year, brillian...
8     [encourag, posit, comment, film, look, forward...
10    [phil, alien, quirki, film, humour, base, odd,...
11    [movi, come, recal, scariest, scene, bird, eat...
12    [boll

In [9]:
# Making Positive and Negative Dictionaries
pos_dictionary = gensim.corpora.Dictionary(pos_processed_documents)
count = 0
print("\nSome random positive words in our dictionary: ")
for k, v in pos_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break    
neg_dictionary = gensim.corpora.Dictionary(neg_processed_documents)
count = 0
print("\nSome random negative words in our dictionary: ")
for k, v in neg_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break


Some random positive words in our dictionary: 
0 accustom
1 agenda
2 agreement
3 appeal
4 aryan
5 audienc
6 away
7 bitch
8 brutal
9 call
10 cell

Some random negative words in our dictionary: 
0 argu
1 basic
2 boogeyman
3 closet
4 decid
5 descent
6 dialog
7 divorc
8 drama
9 expect
10 famili


In [10]:
# Making Postiive and Negative LDA Models
pos_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
pos_bow_corpus = [pos_dictionary.doc2bow(doc) for doc in pos_processed_documents]
pos_lda_model = gensim.models.LdaMulticore(pos_bow_corpus, num_topics=150, id2word=pos_dictionary, passes=10, workers=2)

neg_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
neg_bow_corpus = [neg_dictionary.doc2bow(doc) for doc in neg_processed_documents]
neg_lda_model = gensim.models.LdaMulticore(neg_bow_corpus, num_topics=150, id2word=neg_dictionary, passes=10, workers=2)

In [11]:
# Viewing the LDA Model Topic Results
print("\nFirst Ten Positive Review Topics:")
for idx, topic in pos_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break
print("\nFirst Ten Negative Review Topics")
for idx, topic in neg_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break


First Ten Positive Review Topics:
Topic: 0 
Words: 0.032*"team" + 0.020*"like" + 0.019*"sport" + 0.019*"role" + 0.019*"play" + 0.016*"footbal" + 0.015*"actor" + 0.013*"good" + 0.012*"basebal" + 0.012*"great"
Topic: 1 
Words: 0.018*"urban" + 0.013*"charact" + 0.012*"luci" + 0.011*"virgin" + 0.010*"play" + 0.010*"earli" + 0.010*"style" + 0.010*"right" + 0.009*"offens" + 0.008*"year"
Topic: 2 
Words: 0.021*"charact" + 0.013*"scene" + 0.010*"work" + 0.008*"director" + 0.007*"stori" + 0.007*"point" + 0.006*"make" + 0.006*"perform" + 0.006*"effect" + 0.005*"camera"
Topic: 3 
Words: 0.098*"releas" + 0.048*"christma" + 0.045*"comment" + 0.019*"avail" + 0.017*"print" + 0.017*"spanish" + 0.017*"year" + 0.016*"review" + 0.015*"holiday" + 0.014*"classic"
Topic: 4 
Words: 0.026*"richard" + 0.023*"play" + 0.020*"jean" + 0.017*"role" + 0.017*"gangster" + 0.016*"cagney" + 0.016*"joan" + 0.014*"warner" + 0.011*"star" + 0.011*"bull"
Topic: 5 
Words: 0.039*"king" + 0.026*"british" + 0.015*"play" + 0.014

In [12]:
from gensim.models import CoherenceModel

# Compute Perplexity
print('\nPositive Perplexity: ', pos_lda_model.log_perplexity(pos_bow_corpus))  # a measure of how good the model is. lower the better.
# Compute Coherence Score
pos_coherence_model_lda = CoherenceModel(model=pos_lda_model, texts=pos_processed_documents, dictionary=pos_dictionary, coherence='c_v')
pos_coherence_lda = pos_coherence_model_lda.get_coherence()
print('Positive Coherence Score: ', pos_coherence_lda)
'''Negative Topics'''
# Compute Perplexity
print('\nNegative Perplexity: ', neg_lda_model.log_perplexity(neg_bow_corpus))  # a measure of how good the model is. lower the better.
# Compute Coherence Score
neg_coherence_model_lda = CoherenceModel(model=neg_lda_model, texts=neg_processed_documents, dictionary=neg_dictionary, coherence='c_v')
neg_coherence_lda = neg_coherence_model_lda.get_coherence()
print('Negative Coherence Score: ', neg_coherence_lda)


Positive Perplexity:  -8.092779089657531
Positive Coherence Score:  0.3169594388992144

Negative Perplexity:  -8.164564207702465
Negative Coherence Score:  0.30455843070764493


In [ ]:
#import gensim

#'''Positive'''
# Download File: http://mallet.cs.umass.edu/dist/mallet-2.0.8.zip
#mallet_path = r'C:/MALLET/bin/mallet.bat' # update this path
#pos_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=pos_bow_corpus, num_topics=30, id2word=pos_dictionary)

# Show Topics
#print(pos_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#pos_coherence_model_ldamallet = CoherenceModel(model=pos_ldamallet, texts=pos_processed, dictionary=pos_dictionary, coherence='c_v')
#pos_coherence_ldamallet = pos_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', pos_coherence_ldamallet)

#'''Negative'''
#neg_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=neg_bow_corpus, num_topics=30, id2word=neg_dictionary)

# Show Topics
#print(neg_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#neg_coherence_model_ldamallet = CoherenceModel(model=neg_ldamallet, texts=neg_processed, dictionary=neg_dictionary, coherence='c_v')
#neg_coherence_ldamallet = neg_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', neg_coherence_ldamallet)

In [13]:
import pyLDAvis
import pyLDAvis.gensim

# Visualize positive topic words
pyLDAvis.enable_notebook()
pos_vis = pyLDAvis.gensim.prepare(pos_lda_model, pos_bow_corpus, pos_dictionary)
pos_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
111    0.216653 -0.012923       1        1  5.351725
2      0.094133  0.044529       2        1  3.857754
112    0.183555 -0.170234       3        1  3.748221
109    0.171161 -0.071847       4        1  3.081087
58     0.132801  0.196553       5        1  2.644853
...         ...       ...     ...      ...       ...
57    -0.116140  0.078990     146        1  0.267671
68    -0.009543  0.011562     147        1  0.264684
126   -0.151173 -0.078465     148        1  0.250929
31    -0.082924 -0.043951     149        1  0.237657
27    -0.160353  0.012445     150        1  0.202012

[150 rows x 5 columns], topic_info=        Term         Freq        Total  Category  logprob  loglift
333     seri  4012.000000  4012.000000   Default  30.0000  30.0000
492    music  5333.000000  5333.000000   Default  29.0000  29.0000
26    episod  3069.000000  3069.000000   Default  28.0000  28.0000
107   comedi  4174.000000  4174.000000   Default  27.0000  27.0000
1095    book  2550.000000  2550.000000   Default  26.0000  26.0000
...      ...          ...          ...       ...      ...      ...
733     save    34.898697  1012.344727  Topic150  -4.8400   2.8370
514      rat    34.193340  1436.024170  Topic150  -4.8604   2.4670
1270    type    31.986174  1423.129395  Topic150  -4.9272   2.4093
656    cours    29.521935  2611.006104  Topic150  -5.0073   1.7222
1510   earli    28.650339  1876.940063  Topic150  -5.0373   2.0224

[8751 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
5450    127  0.958146   aamir
4769      8  0.018788   aaron
4769     11  0.084547   aaron
4769     28  0.159700   aaron
4769     74  0.554253   aaron
...     ...       ...     ...
1439     61  0.097141    zone
1439     78  0.728557    zone
1439    117  0.013877    zone
7671    147  0.992242   zorro
4492     54  0.964261  zucker

[61829 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[112, 3, 113, 110, 59, 115, 84, 78, 118, 149, 26, 7, 87, 137, 130, 101, 146, 109, 80, 133, 50, 45, 135, 29, 134, 93, 92, 22, 85, 123, 148, 97, 63, 116, 43, 75, 114, 120, 119, 1, 30, 90, 125, 48, 34, 52, 15, 82, 5, 141, 96, 56, 132, 2, 70, 124, 150, 9, 60, 44, 37, 35, 99, 31, 86, 12, 74, 47, 18, 17, 24, 105, 4, 39, 6, 147, 13, 65, 49, 122, 54, 68, 89, 11, 41, 8, 91, 14, 16, 76, 83, 27, 62, 51, 129, 55, 94, 108, 25, 142, 38, 126, 102, 10, 33, 73, 106, 140, 53, 67, 117, 61, 21, 36, 57, 71, 66, 40, 79, 131, 95, 98, 139, 111, 23, 46, 42, 144, 77, 136, 145, 64, 88, 103, 19, 143, 128, 81, 72, 20, 138, 121, 100, 104, 107, 58, 69, 127, 32, 28])

In [14]:
# Visualize negative topic words
pyLDAvis.enable_notebook()
neg_vis = pyLDAvis.gensim.prepare(neg_lda_model, neg_bow_corpus, neg_dictionary)
neg_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
18    -0.203378 -0.019000       1        1  3.165384
74    -0.202834 -0.082403       2        1  3.132685
129   -0.161196 -0.025174       3        1  2.983948
92    -0.130650  0.055081       4        1  2.928886
10    -0.206043 -0.035966       5        1  2.792589
...         ...       ...     ...      ...       ...
128    0.030583 -0.068231     146        1  0.261551
78     0.106578 -0.001738     147        1  0.256962
70     0.208251  0.005955     148        1  0.247093
132    0.165099 -0.053351     149        1  0.222532
113    0.213824 -0.048224     150        1  0.205012

[150 rows x 5 columns], topic_info=          Term          Freq         Total  Category  logprob  loglift
1491      book   3111.000000   3111.000000   Default  30.0000  30.0000
163     horror   4455.000000   4455.000000   Default  29.0000  29.0000
128    charact  15056.000000  15056.000000   Default  28.0000  28.0000
71      origin   4386.000000   4386.000000   Default  27.0000  27.0000
60       funni   4704.000000   4704.000000   Default  26.0000  26.0000
...        ...           ...           ...       ...      ...      ...
1948  advantag     46.737415    144.887802  Topic150  -4.4986   5.0584
1053     appli     44.723629    185.080582  Topic150  -4.5426   4.7696
2358     heavi     49.698448    415.875214  Topic150  -4.4371   4.0654
604      press     38.603901    190.521439  Topic150  -4.6897   4.5934
3119    vehicl     38.566017    279.550903  Topic150  -4.6907   4.2090

[8614 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
5660     21  0.782997    aaron
5660    103  0.195749    aaron
5660    138  0.013050    aaron
3168      3  0.120198  abandon
3168      4  0.030049  abandon
...     ...       ...      ...
3002     43  0.434214     zone
3002     66  0.140481     zone
3002    150  0.063855     zone
7195     46  0.970679    zucco
7654      8  0.963877   zucker

[63693 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[19, 75, 130, 93, 11, 87, 67, 134, 13, 9, 42, 66, 23, 40, 136, 30, 26, 115, 149, 84, 105, 138, 22, 127, 3, 74, 111, 33, 52, 132, 73, 77, 5, 131, 36, 50, 25, 59, 145, 78, 7, 96, 122, 39, 16, 15, 150, 57, 94, 97, 46, 17, 143, 103, 106, 27, 44, 8, 76, 37, 43, 104, 146, 117, 62, 51, 91, 53, 38, 113, 109, 89, 72, 31, 24, 118, 125, 116, 144, 55, 92, 112, 58, 140, 82, 69, 34, 65, 128, 85, 35, 18, 119, 135, 48, 10, 141, 95, 2, 32, 100, 120, 102, 108, 60, 29, 110, 137, 83, 86, 147, 139, 98, 6, 4, 126, 80, 21, 81, 90, 56, 121, 12, 28, 88, 47, 49, 54, 1, 45, 68, 101, 63, 64, 70, 20, 107, 142, 41, 124, 99, 61, 148, 123, 14, 129, 79, 71, 133, 114])

In [40]:
def get_sentiment(text):
    count = 0
    pos_score = 0
    neg_score = 0
    #get what positive topics might be related
    bow_vector = pos_dictionary.doc2bow(preprocess(text))
    
    for idx, score in sorted(pos_lda_model[bow_vector], key=lambda tup:-1*tup[1]):
        count+=1
        pos_score += score
        if count > 2:
            break
    pos_score = pos_score/3
    pos_score *= 100
    
    count = 0
    #get what negative topics might be related
    bow_vector = neg_dictionary.doc2bow(preprocess(text))
    for idx, score in sorted(neg_lda_model[bow_vector], key=lambda tup:-1*tup[1]):    
        neg_score += score
        count+=1
        if count > 2:
            break
    neg_score = neg_score/3
    neg_score *= 100
    
    result = 0
    if pos_score>neg_score:
        result = (pos_score - neg_score)/(pos_score + neg_score)
        result *= 100
        result = 50 + (result*2)
        return result
    else:
        result = (neg_score - pos_score)/(pos_score + neg_score)
        result *= 100
        result = 50+(result*2)
        return result

In [49]:
unseen_movie_description = input("Please enter a movie description to analyze: ")
print("\nWe predict that {}% will like this movie".format(get_sentiment(unseen_movie_description)))

Please enter a movie description to analyze: Michael Newman (Adam Sandler) seems to have it all but his wife, Donna (Kate Beckinsale), is increasingly frustrated by the amount of time he has to spend at work. Michael cannot find time to be at home until he meets an eccentric inventor (Christopher Walken) who gives him a universal remote that controls time. At first he happily skips the boring times until he realizes the remote is in control of his life and he learns to cherish all the precious moments with his family.

We predict that 52.40934386740079% will like this movie
